In [32]:
import pandas as pd

dados_datatran = []
for ii in range(2017,2020):
    csv = './datasets/datatran' + str(ii) + '.csv' 
  
    dado = pd.read_csv(csv, encoding = "ISO-8859-1", sep=';', engine='python', error_bad_lines=False)
    dados_datatran.append(dado)
    
datatran = pd.concat(dados_datatran, ignore_index=True)

In [ ]:
import plotly.plotly as py
import plotly.graph_objs as go
import plotly.offline as offline

br_acidentes_count = datatran.br.dropna().astype(int).astype(str).value_counts().sort_values(ascending=False)
br_acidentes_count.index = 'BR ' + br_acidentes_count.index 

br_acidentes_bar = go.Bar(x=br_acidentes_count.index,
                          y=br_acidentes_count.values,
                          marker=dict(color='rgb(180, 20, 20)'))

data_quantidade_bar = [br_acidentes_bar]

layout_quantidade_bar = go.Layout(title="Acidentes em Rodovias Federais",
        font={'size':10},
        xaxis=go.layout.XAxis(title=go.layout.xaxis.Title(text='Rodovias Federais',font=dict(size=18))),
        yaxis=go.layout.YAxis(title=go.layout.yaxis.Title(text='Quantidade de Acidentes',font=dict(size=18,)))
    )

fig_quantidade_bar = go.Figure(data=data_quantidade_bar,layout=layout_quantidade_bar)
offline.plot(fig_quantidade_bar,filename='bar_br_count.html')

In [81]:
import folium
import requests
import geocoder

headers = {
    'Content-Type': 'application/json;charset=UTF-8',
    'User-Agent': 'google-colab',
    'Accept': 'application/json, text/plain, */*',
    'Accept-Encoding': 'gzip, deflate, br',
    'Accept-Language': 'pt-BR,pt;q=0.9,en-US;q=0.8,en;q=0.7',
    'Connection': 'keep-alive',
}

response = requests.get("https://servicodados.ibge.gov.br/api/v2/malhas/"+
                        "?formato=application/vnd.geo+json&resolucao=2",
                       headers=headers)
brazil_json = response.json()

brazil_geo = geocoder.arcgis("Brazil")
m = folium.Map(location=brazil_geo.latlng,zoom_start=4,tiles='Open Street Map')

folium.Choropleth(geo_data=brazil_json, line_weight=2, fill_opacity=0, name='Marcação das UFs').add_to(m)
m

In [ ]:
identificador_estados = requests.get('https://servicodados.ibge.gov.br/api/v1/localidades/estados',
                       headers=headers).json()

id_sigla = {}
for estado in identificador_estados:
    id_sigla[str(estado['id'])] = estado['sigla']

In [ ]:
top_n_rodovias = 3

rodovias_estados_geojsons = {}
rodovias_acidentes_latlng = {}
rodovias = datatran.br.dropna().value_counts().head(top_n_rodovias).index

for rodovia_ranking in range(0,top_n_rodovias):
    rodovia = rodovias[rodovia_ranking]
    
    # estados que cada rodovia passa, ou pelo menos há registro de acidente
    estados_ocorrencias_rodovia = datatran[datatran.br == rodovia].uf.value_counts()
    
    rodovias_estados_geojsons[rodovia] = requests.get("https://servicodados.ibge.gov.br/api/v2/malhas/"+
                                        "?formato=application/vnd.geo+json&resolucao=2",
                                       headers=headers).json()
    features_estados_rodovia = []
    for index in range(0,len(brazil_json['features'])):
        if id_sigla[rodovias_estados_geojsons[rodovia]['features'][index]['properties']['codarea']] in estados_ocorrencias_rodovia.index:
            features_estados_rodovia.append(rodovias_estados_geojsons[rodovia]['features'][index])
            
    rodovias_estados_geojsons[rodovia]['features'] = features_estados_rodovia
    
    # latitudes e longitudes de cada rodovia
    rodovias_acidentes_latlng[rodovia] = [[row.latitude,row.longitude] for index,row in datatran[datatran.br == rodovia].iterrows()]

In [ ]:
from folium.plugins import HeatMap, FeatureGroupSubGroup
from folium.map import Layer
from folium import LayerControl, FeatureGroup

m = folium.Map(location=brazil_geo.latlng,zoom_start=4)
folium.TileLayer(tiles='openstreetmap',control=False,overlay=True).add_to(m)

for rodovia_ranking in range(0,top_n_rodovias):
    group = FeatureGroup(name='BR ' + str(int(rodovias[rodovia_ranking])),overlay=False)
    HeatMap(data=rodovias_acidentes_latlng[rodovias[rodovia_ranking]]).add_to(group)
    folium.Choropleth(geo_data=rodovias_estados_geojsons[rodovias[rodovia_ranking]], line_weight=2, fill_opacity=0).add_to(group)
    group.add_to(m)

LayerControl().add_to(m)

In [78]:
dia_acidente_latlng = pd.DataFrame(datatran[['data_inversa','latitude','longitude']])
dia_acidente_latlng.data_inversa = dia_acidente_latlng.data_inversa.apply(lambda x: x.split('-')[1] + '-' + x.split('-')[0])
dia_acidente_latlng.latitude = dia_acidente_latlng[['latitude','longitude']].values.tolist()
dia_acidente_latlng.drop(columns=['longitude'],inplace=True)
dia_acidente_latlng.rename(columns={'data_inversa':'mes_ano','latitude':'latlng'},inplace=True)

datas_acidentes_indexes = []
latlng_acidentes = []

for index,value in dia_acidente_latlng.groupby('mes_ano')['latlng'].apply(list).items():
    datas_acidentes_indexes.append(index)
    latlng_acidentes.append(value)

In [83]:
from folium.plugins import HeatMapWithTime

m = folium.Map(location=brazil_geo.latlng,zoom_start=4)

HeatMapWithTime(data=latlng_acidentes,index=datas_acidentes_indexes).add_to(m)

m